In [1]:
# Package Imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

In [2]:
# Data Path
dataPath = "../../Data/Toxic-Thread-Detector/jigsaw-toxic"
train = pd.read_csv(dataPath + "/train.csv")
test = pd.read_csv(dataPath + "/test.csv")

In [3]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\xil14\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [20]:
import re
from tqdm import tqdm_notebook

from nltk.corpus import stopwords
from sklearn.model_selection import train_test_split
from tensorflow.keras import regularizers, initializers, optimizers, callbacks
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.preprocessing.text import Tokenizer
from keras.utils.np_utils import to_categorical
from tensorflow.keras.layers import *
from tensorflow.keras.models import Model

In [4]:
MAX_NB_WORDS = 100000    # max no. of words for tokenizer
MAX_SEQUENCE_LENGTH = 200 # max length of each entry (sentence), including padding
VALIDATION_SPLIT = 0.2   # data for validation (not used in training)
EMBEDDING_DIM = 100      # embedding dimensions for word vectors (word2vec/GloVe)
GLOVE_DIR = "../../Data/Toxic-Thread-Detector/glove/glove.6B."+str(EMBEDDING_DIM)+"d.txt"

In [11]:
def clean_text(text, remove_stopwords = True):
    output = ""
    text = str(text).replace("\n", "")
    text = re.sub(r'[^\w\s]','',text).lower()
    if remove_stopwords:
        text = text.split(" ")
        for word in text:
            if word not in stopwords.words("english"):
                output = output + " " + word
    else:
        output = text
    return str(output.strip())[1:-3].replace("  ", " ")

def preprocessing_train(test):
    MAX_NB_WORDS = 100000    # max no. of words for tokenizer
    MAX_SEQUENCE_LENGTH = 200 # max length of each entry (sentence), including padding
    VALIDATION_SPLIT = 0.2   # data for validation (not used in training)
    EMBEDDING_DIM = 100      # embedding dimensions for word vectors (word2vec/GloVe)
    GLOVE_DIR = "../../Data/Toxic-Thread-Detector/glove/glove.6B."+str(EMBEDDING_DIM)+"d.txt"
    texts = [] 
    tokenizer = Tokenizer(num_words=MAX_NB_WORDS)
    for line in tqdm_notebook(test, total=len(test)): 
        texts.append(clean_text(line))
    tokenizer.fit_on_texts(texts)
    sequences = tokenizer.texts_to_sequences(texts)
    word_index = tokenizer.word_index
    data = pad_sequences(sequences, padding = 'post', maxlen = MAX_SEQUENCE_LENGTH)
    return data, tokenizer

def preprocessing_test(test, tokenizer):
    MAX_NB_WORDS = 100000    # max no. of words for tokenizer
    MAX_SEQUENCE_LENGTH = 200 # max length of each entry (sentence), including padding
    VALIDATION_SPLIT = 0.2   # data for validation (not used in training)
    EMBEDDING_DIM = 100      # embedding dimensions for word vectors (word2vec/GloVe)
    GLOVE_DIR = "../../Data/Toxic-Thread-Detector/glove/glove.6B."+str(EMBEDDING_DIM)+"d.txt"
    texts = [] 

    for line in tqdm_notebook(test, total=len(test)): 
        texts.append(clean_text(line))
    tokenizer.fit_on_texts(texts)
    sequences = tokenizer.texts_to_sequences(texts)
    word_index = tokenizer.word_index
    data = pad_sequences(sequences, padding = 'post', maxlen = MAX_SEQUENCE_LENGTH)
    return data

In [12]:
X = train["comment_text"]
X, tokenizer = preprocessing_train(X)

In [18]:
y = train[["toxic", "severe_toxic", "obscene", "threat", "insult", "identity_hate"]]

In [21]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=42)

In [22]:
# First output
y1_train = y_train[["toxic"]].values
y1_test =  y_test[["toxic"]].values

# Second output
y2_train = y_train[["severe_toxic"]].values
y2_test =  y_test[["severe_toxic"]].values

# Third output
y3_train = y_train[["obscene"]].values
y3_test =  y_test[["obscene"]].values

# Fourth output
y4_train = y_train[["threat"]].values
y4_test =  y_test[["threat"]].values

# Fifth output
y5_train = y_train[["insult"]].values
y5_test =  y_test[["insult"]].values

# Sixth output
y6_train = y_train[["identity_hate"]].values
y6_test =  y_test[["identity_hate"]].values

In [28]:
word_index = tokenizer.word_index

embeddings_index = {}
f = open(GLOVE_DIR,encoding="utf8")
print('Loading GloVe from:', GLOVE_DIR,'...', end='')
for line in f:
    values = line.split()
    word = values[0]
    embeddings_index[word] = np.asarray(values[1:], dtype='float32')
f.close()
print("Done.\n Proceeding with Embedding Matrix...", end="")

embedding_matrix = np.random.random((len(word_index) + 1, EMBEDDING_DIM))
for word, i in word_index.items():
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        embedding_matrix[i] = embedding_vector
print(" Completed!")

Loading GloVe from: ../../Data/Toxic-Thread-Detector/glove/glove.6B.100d.txt ...Done.
 Proceeding with Embedding Matrix... Completed!


In [69]:
vocab_size = len(word_index)+1
input_1 = Input(shape=(200,))
embedding_layer = Embedding(vocab_size, 100, weights=[embedding_matrix], trainable=False)(input_1)
LSTM_Layer1 = LSTM(128)(embedding_layer)

output1 = Dense(1, activation='sigmoid')(LSTM_Layer1)
output2 = Dense(1, activation='sigmoid')(LSTM_Layer1)
output3 = Dense(1, activation='sigmoid')(LSTM_Layer1)
output4 = Dense(1, activation='sigmoid')(LSTM_Layer1)
output5 = Dense(1, activation='sigmoid')(LSTM_Layer1)
output6 = Dense(1, activation='sigmoid')(LSTM_Layer1)

model = Model(inputs=input_1, outputs=[output1, output2, output3, output4, output5, output6])
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['acc'])

In [70]:
print(model.summary())

Model: "model_3"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_6 (InputLayer)            [(None, 200)]        0                                            
__________________________________________________________________________________________________
embedding_3 (Embedding)         (None, 200, 100)     32467000    input_6[0][0]                    
__________________________________________________________________________________________________
lstm_3 (LSTM)                   (None, 128)          117248      embedding_3[0][0]                
__________________________________________________________________________________________________
dense_18 (Dense)                (None, 1)            129         lstm_3[0][0]                     
____________________________________________________________________________________________

In [105]:
history = model.fit(x=X_train, y=[y1_train, y2_train, y3_train, y4_train, y5_train, y6_train], batch_size=32, epochs=5, verbose=1, validation_split=0.2)

Train on 102124 samples, validate on 25532 samples
Epoch 1/5


   864/102124 [..............................] - ETA: 16:16 - loss: 0.3293 - dense_18_loss: 0.0746 - dense_19_loss: 0.0059 - dense_20_loss: 0.0314 - dense_21_loss: 0.0050 - dense_22_loss: 0.0479 - dense_23_loss: 0.1645 - dense_18_acc: 1.0000 - dense_19_acc: 1.0000 - dense_20_acc: 1.0000 - dense_21_acc: 1.0000 - dense_22_acc: 1.0000 - dense_23_acc: 0.96 - ETA: 15:00 - loss: 0.3454 - dense_18_loss: 0.1384 - dense_19_loss: 0.0054 - dense_20_loss: 0.0673 - dense_21_loss: 0.0046 - dense_22_loss: 0.0431 - dense_23_loss: 0.0866 - dense_18_acc: 0.9688 - dense_19_acc: 1.0000 - dense_20_acc: 0.9844 - dense_21_acc: 1.0000 - dense_22_acc: 1.0000 - dense_23_acc: 0.98 - ETA: 14:47 - loss: 0.3873 - dense_18_loss: 0.1396 - dense_19_loss: 0.0049 - dense_20_loss: 0.0520 - dense_21_loss: 0.0041 - dense_22_loss: 0.0752 - dense_23_loss: 0.1115 - dense_18_acc: 0.9688 - dense_19_acc: 1.0000 - dense_20_acc: 0.9896 - dense_21_acc: 1.0000 - dense_22_acc: 0.9896 - dense_23_acc: 0.97 - ETA: 14:32 - loss: 0.4752 -

  1728/102124 [..............................] - ETA: 13:33 - loss: 0.7993 - dense_18_loss: 0.2806 - dense_19_loss: 0.0700 - dense_20_loss: 0.1985 - dense_21_loss: 0.0133 - dense_22_loss: 0.1744 - dense_23_loss: 0.0626 - dense_18_acc: 0.9051 - dense_19_acc: 0.9844 - dense_20_acc: 0.9397 - dense_21_acc: 0.9989 - dense_22_acc: 0.9487 - dense_23_acc: 0.98 - ETA: 13:32 - loss: 0.7902 - dense_18_loss: 0.2795 - dense_19_loss: 0.0689 - dense_20_loss: 0.1956 - dense_21_loss: 0.0131 - dense_22_loss: 0.1721 - dense_23_loss: 0.0610 - dense_18_acc: 0.9062 - dense_19_acc: 0.9838 - dense_20_acc: 0.9407 - dense_21_acc: 0.9989 - dense_22_acc: 0.9494 - dense_23_acc: 0.98 - ETA: 13:31 - loss: 0.7802 - dense_18_loss: 0.2781 - dense_19_loss: 0.0670 - dense_20_loss: 0.1929 - dense_21_loss: 0.0128 - dense_22_loss: 0.1702 - dense_23_loss: 0.0593 - dense_18_acc: 0.9062 - dense_19_acc: 0.9844 - dense_20_acc: 0.9417 - dense_21_acc: 0.9990 - dense_22_acc: 0.9500 - dense_23_acc: 0.98 - ETA: 13:30 - loss: 0.7785 -

  2592/102124 [..............................] - ETA: 14:03 - loss: 0.7925 - dense_18_loss: 0.2751 - dense_19_loss: 0.0681 - dense_20_loss: 0.1985 - dense_21_loss: 0.0214 - dense_22_loss: 0.1774 - dense_23_loss: 0.0520 - dense_18_acc: 0.9074 - dense_19_acc: 0.9847 - dense_20_acc: 0.9392 - dense_21_acc: 0.9972 - dense_22_acc: 0.9466 - dense_23_acc: 0.99 - ETA: 14:02 - loss: 0.7908 - dense_18_loss: 0.2760 - dense_19_loss: 0.0674 - dense_20_loss: 0.1979 - dense_21_loss: 0.0211 - dense_22_loss: 0.1771 - dense_23_loss: 0.0513 - dense_18_acc: 0.9068 - dense_19_acc: 0.9849 - dense_20_acc: 0.9392 - dense_21_acc: 0.9972 - dense_22_acc: 0.9464 - dense_23_acc: 0.99 - ETA: 14:03 - loss: 0.7899 - dense_18_loss: 0.2756 - dense_19_loss: 0.0687 - dense_20_loss: 0.1973 - dense_21_loss: 0.0209 - dense_22_loss: 0.1768 - dense_23_loss: 0.0506 - dense_18_acc: 0.9068 - dense_19_acc: 0.9846 - dense_20_acc: 0.9391 - dense_21_acc: 0.9973 - dense_22_acc: 0.9463 - dense_23_acc: 0.99 - ETA: 14:02 - loss: 0.7860 -

  3456/102124 [>.............................] - ETA: 13:41 - loss: 0.7904 - dense_18_loss: 0.2843 - dense_19_loss: 0.0626 - dense_20_loss: 0.1926 - dense_21_loss: 0.0236 - dense_22_loss: 0.1799 - dense_23_loss: 0.0474 - dense_18_acc: 0.9028 - dense_19_acc: 0.9863 - dense_20_acc: 0.9405 - dense_21_acc: 0.9966 - dense_22_acc: 0.9451 - dense_23_acc: 0.99 - ETA: 13:40 - loss: 0.7915 - dense_18_loss: 0.2853 - dense_19_loss: 0.0620 - dense_20_loss: 0.1932 - dense_21_loss: 0.0234 - dense_22_loss: 0.1807 - dense_23_loss: 0.0469 - dense_18_acc: 0.9021 - dense_19_acc: 0.9864 - dense_20_acc: 0.9401 - dense_21_acc: 0.9966 - dense_22_acc: 0.9447 - dense_23_acc: 0.99 - ETA: 13:40 - loss: 0.7906 - dense_18_loss: 0.2845 - dense_19_loss: 0.0628 - dense_20_loss: 0.1927 - dense_21_loss: 0.0232 - dense_22_loss: 0.1808 - dense_23_loss: 0.0465 - dense_18_acc: 0.9029 - dense_19_acc: 0.9862 - dense_20_acc: 0.9405 - dense_21_acc: 0.9967 - dense_22_acc: 0.9446 - dense_23_acc: 0.99 - ETA: 13:39 - loss: 0.7869 -

...

 99360/102124 [============================>.] - ETA: 23s - loss: 0.3334 - dense_18_loss: 0.1261 - dense_19_loss: 0.0232 - dense_20_loss: 0.0653 - dense_21_loss: 0.0134 - dense_22_loss: 0.0781 - dense_23_loss: 0.0272 - dense_18_acc: 0.9541 - dense_19_acc: 0.9906 - dense_20_acc: 0.9776 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.99 - ETA: 23s - loss: 0.3334 - dense_18_loss: 0.1261 - dense_19_loss: 0.0232 - dense_20_loss: 0.0653 - dense_21_loss: 0.0134 - dense_22_loss: 0.0781 - dense_23_loss: 0.0272 - dense_18_acc: 0.9541 - dense_19_acc: 0.9906 - dense_20_acc: 0.9776 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.99 - ETA: 23s - loss: 0.3334 - dense_18_loss: 0.1261 - dense_19_loss: 0.0232 - dense_20_loss: 0.0653 - dense_21_loss: 0.0134 - dense_22_loss: 0.0781 - dense_23_loss: 0.0272 - dense_18_acc: 0.9541 - dense_19_acc: 0.9906 - dense_20_acc: 0.9776 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.99 - ETA: 23s - loss: 0.3333 - dense_1

100224/102124 [============================>.] - ETA: 18s - loss: 0.3335 - dense_18_loss: 0.1263 - dense_19_loss: 0.0232 - dense_20_loss: 0.0652 - dense_21_loss: 0.0135 - dense_22_loss: 0.0782 - dense_23_loss: 0.0271 - dense_18_acc: 0.9540 - dense_19_acc: 0.9906 - dense_20_acc: 0.9776 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.99 - ETA: 17s - loss: 0.3335 - dense_18_loss: 0.1262 - dense_19_loss: 0.0232 - dense_20_loss: 0.0652 - dense_21_loss: 0.0135 - dense_22_loss: 0.0782 - dense_23_loss: 0.0271 - dense_18_acc: 0.9541 - dense_19_acc: 0.9906 - dense_20_acc: 0.9776 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.99 - ETA: 17s - loss: 0.3335 - dense_18_loss: 0.1262 - dense_19_loss: 0.0232 - dense_20_loss: 0.0652 - dense_21_loss: 0.0135 - dense_22_loss: 0.0782 - dense_23_loss: 0.0272 - dense_18_acc: 0.9541 - dense_19_acc: 0.9906 - dense_20_acc: 0.9776 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.99 - ETA: 17s - loss: 0.3337 - dense_1

101088/102124 [============================>.] - ETA: 12s - loss: 0.3331 - dense_18_loss: 0.1260 - dense_19_loss: 0.0233 - dense_20_loss: 0.0651 - dense_21_loss: 0.0135 - dense_22_loss: 0.0781 - dense_23_loss: 0.0271 - dense_18_acc: 0.9542 - dense_19_acc: 0.9906 - dense_20_acc: 0.9776 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.99 - ETA: 12s - loss: 0.3333 - dense_18_loss: 0.1261 - dense_19_loss: 0.0232 - dense_20_loss: 0.0652 - dense_21_loss: 0.0135 - dense_22_loss: 0.0782 - dense_23_loss: 0.0271 - dense_18_acc: 0.9542 - dense_19_acc: 0.9906 - dense_20_acc: 0.9776 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.99 - ETA: 11s - loss: 0.3333 - dense_18_loss: 0.1261 - dense_19_loss: 0.0232 - dense_20_loss: 0.0652 - dense_21_loss: 0.0135 - dense_22_loss: 0.0782 - dense_23_loss: 0.0271 - dense_18_acc: 0.9542 - dense_19_acc: 0.9906 - dense_20_acc: 0.9776 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.99 - ETA: 11s - loss: 0.3333 - dense_1

101952/102124 [============================>.] - ETA: 6s - loss: 0.3333 - dense_18_loss: 0.1261 - dense_19_loss: 0.0232 - dense_20_loss: 0.0653 - dense_21_loss: 0.0135 - dense_22_loss: 0.0782 - dense_23_loss: 0.0272 - dense_18_acc: 0.9542 - dense_19_acc: 0.9906 - dense_20_acc: 0.9775 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.991 - ETA: 6s - loss: 0.3333 - dense_18_loss: 0.1260 - dense_19_loss: 0.0232 - dense_20_loss: 0.0653 - dense_21_loss: 0.0135 - dense_22_loss: 0.0782 - dense_23_loss: 0.0272 - dense_18_acc: 0.9542 - dense_19_acc: 0.9906 - dense_20_acc: 0.9775 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.991 - ETA: 6s - loss: 0.3333 - dense_18_loss: 0.1260 - dense_19_loss: 0.0232 - dense_20_loss: 0.0652 - dense_21_loss: 0.0135 - dense_22_loss: 0.0781 - dense_23_loss: 0.0272 - dense_18_acc: 0.9542 - dense_19_acc: 0.9906 - dense_20_acc: 0.9776 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.991 - ETA: 6s - loss: 0.3333 - dense_18

102124/102124 [==============================] - ETA: 0s - loss: 0.3333 - dense_18_loss: 0.1262 - dense_19_loss: 0.0231 - dense_20_loss: 0.0653 - dense_21_loss: 0.0135 - dense_22_loss: 0.0780 - dense_23_loss: 0.0271 - dense_18_acc: 0.9541 - dense_19_acc: 0.9906 - dense_20_acc: 0.9775 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.991 - ETA: 0s - loss: 0.3332 - dense_18_loss: 0.1262 - dense_19_loss: 0.0231 - dense_20_loss: 0.0653 - dense_21_loss: 0.0134 - dense_22_loss: 0.0780 - dense_23_loss: 0.0271 - dense_18_acc: 0.9541 - dense_19_acc: 0.9906 - dense_20_acc: 0.9775 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.991 - ETA: 0s - loss: 0.3333 - dense_18_loss: 0.1262 - dense_19_loss: 0.0231 - dense_20_loss: 0.0653 - dense_21_loss: 0.0134 - dense_22_loss: 0.0781 - dense_23_loss: 0.0271 - dense_18_acc: 0.9541 - dense_19_acc: 0.9906 - dense_20_acc: 0.9775 - dense_21_acc: 0.9969 - dense_22_acc: 0.9708 - dense_23_acc: 0.991 - ETA: 0s - loss: 0.3333 - dense_18

In [106]:
score = model.evaluate(x=X_test, y=[y1_test, y2_test, y3_test, y4_test, y5_test, y6_test], verbose=1)

31915/1 [===============================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

 - 117s 4ms/sample - loss: 0.7071 - dense_18_loss: 0.1417 - dense_19_loss: 0.0273 - dense_20_loss: 0.0784 - dense_21_loss: 0.0105 - dense_22_loss: 0.0910 - dense_23_loss: 0.0333 - dense_18_acc: 0.9490 - dense_19_acc: 0.9904 - dense_20_acc: 0.9733 - dense_21_acc: 0.9977 - dense_22_acc: 0.9658 - dense_23_acc: 0.9911


In [107]:
comments = "Really stupid in this place. fuck off you troll!"
comments = pd.Series(comments)
comments_1 = preprocessing_test(comments, tokenizer)

In [108]:
pred = model.predict(comments_1)
result = []
labels = ["toxic", "severe_toxic", "obscene", "threat", "insult", "identity_hate"]
for p in pred:
    result.append(float(p[0]))
print(dict(zip(labels, result)))

{'toxic': 0.9196690917015076, 'severe_toxic': 0.025544999167323112, 'obscene': 0.7885405421257019, 'threat': 0.0068905968219041824, 'insult': 0.42700138688087463, 'identity_hate': 0.02542535960674286}


In [109]:
import h5py
model.save('ltsm_model.h5', save_format = 'tf')

In [110]:
from keras.utils import CustomObjectScope
from keras.initializers import glorot_uniform
from tensorflow.keras.models import load_model
with CustomObjectScope({'GlorotUniform': glorot_uniform()}):
    new_model_2 = load_model('ltsm_model.h5')

In [111]:
new_model_2.predict(comments_1)

[array([[0.9196691]], dtype=float32),
 array([[0.025545]], dtype=float32),
 array([[0.78854054]], dtype=float32),
 array([[0.0068906]], dtype=float32),
 array([[0.4270014]], dtype=float32),
 array([[0.02542536]], dtype=float32)]

In [114]:
# save tokenizer
import json
tokenizer_json = tokenizer.to_json()
with open('tokenizer.json', 'w', encoding='utf-8') as f:
    f.write(json.dumps(tokenizer_json, ensure_ascii=False))

In [116]:
from keras_preprocessing.text import tokenizer_from_json
with open('tokenizer.json') as f:
    data = json.load(f)
    tokenizer = tokenizer_from_json(data)